In [1]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import plotly.express as px

In [2]:
# read dataframe

df = pd.read_csv('time_series_30min_singleindex.csv')
df['utc_timestamp'] = pd.to_datetime(df['utc_timestamp'])
print(df.columns)
time_load_df = df[['utc_timestamp', 'IE_load_actual_entsoe_transparency']]

Index(['utc_timestamp', 'cet_cest_timestamp',
       'CY_load_actual_entsoe_transparency',
       'CY_load_forecast_entsoe_transparency',
       'CY_wind_onshore_generation_actual',
       'GB_GBN_load_actual_entsoe_transparency',
       'GB_GBN_load_forecast_entsoe_transparency', 'GB_GBN_solar_capacity',
       'GB_GBN_solar_generation_actual', 'GB_GBN_solar_profile',
       'GB_GBN_wind_capacity', 'GB_GBN_wind_generation_actual',
       'GB_GBN_wind_profile', 'GB_GBN_wind_offshore_capacity',
       'GB_GBN_wind_offshore_generation_actual',
       'GB_GBN_wind_offshore_profile', 'GB_GBN_wind_onshore_capacity',
       'GB_GBN_wind_onshore_generation_actual', 'GB_GBN_wind_onshore_profile',
       'GB_NIR_load_actual_entsoe_transparency',
       'GB_NIR_load_forecast_entsoe_transparency', 'GB_NIR_solar_capacity',
       'GB_NIR_wind_onshore_capacity', 'GB_NIR_wind_onshore_generation_actual',
       'GB_UKM_load_actual_entsoe_transparency',
       'GB_UKM_load_forecast_entsoe_transparency

In [3]:
time_load_df = time_load_df.dropna()
time_load_df.reset_index(drop=True, inplace=True)
time_load_df.head(10)

utc_timestamp  IE_load_actual_entsoe_transparency
0 2015-01-01 00:30:00+00:00                             2832.37
1 2015-01-01 01:00:00+00:00                             2726.20
2 2015-01-01 01:30:00+00:00                             2629.74
3 2015-01-01 02:00:00+00:00                             2487.61
4 2015-01-01 02:30:00+00:00                             2376.85
5 2015-01-01 03:00:00+00:00                             2311.84
6 2015-01-01 03:30:00+00:00                             2239.74
7 2015-01-01 04:00:00+00:00                             2166.52
8 2015-01-01 04:30:00+00:00                             2179.93
9 2015-01-01 05:00:00+00:00                             2139.69

In [4]:
px.line(time_load_df, x='utc_timestamp', y='IE_load_actual_entsoe_transparency', title='Load in Cyprus')


In [5]:
time_load_df.columns = ['time', 'value']

In [6]:
from TimeseriesDatasets import TimeseriesOverlapDataset, TimeseriesRollingDataset

# split into train for 2015-2018, val for 2018-01 to 2018-6, test for 2018-07 to 2020-01

train_df = time_load_df[time_load_df['time'] < '2018-01-01']
val_df = time_load_df[(time_load_df['time'] >= '2018-01-01') & (time_load_df['time'] < '2018-07-01')]
test_df = time_load_df[(time_load_df['time'] >= '2018-07-01') & (time_load_df['time'] < '2020-01-01')]

trainds = TimeseriesOverlapDataset(train_df, 24*7*2, stride = 10)
valds = TimeseriesOverlapDataset(val_df, 24*7*2, stride = 10)
testds = TimeseriesRollingDataset(test_df, 24*7*2)

print(len(trainds), len(valds), len(testds))

                       time     value  year  month  weekday  day  hour  minute
0 2015-01-01 00:30:00+00:00 -0.441375  2015      1        3    1     0      30
1 2015-01-01 01:00:00+00:00 -0.619303  2015      1        3    1     1       0
2 2015-01-01 01:30:00+00:00 -0.780959  2015      1        3    1     1      30
3 2015-01-01 02:00:00+00:00 -1.019153  2015      1        3    1     2       0
4 2015-01-01 02:30:00+00:00 -1.204774  2015      1        3    1     2      30
                           time     value  year  month  weekday  day  hour  \
52277 2018-01-01 00:00:00+00:00 -0.534499  2018      1        0    1     0   
52278 2018-01-01 00:30:00+00:00 -0.617366  2018      1        0    1     0   
52279 2018-01-01 01:00:00+00:00 -0.800100  2018      1        0    1     1   
52280 2018-01-01 01:30:00+00:00 -0.959063  2018      1        0    1     1   
52281 2018-01-01 02:00:00+00:00 -1.141212  2018      1        0    1     2   

       minute  
52277       0  
52278      30  
52279    

c:\Users\Fernando Caro\Documents\CODE\py\LoadForecasting\TimeseriesDatasets.py:16: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

c:\Users\Fernando Caro\Documents\CODE\py\LoadForecasting\TimeseriesDatasets.py:17: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

c:\Users\Fernando Caro\Documents\CODE\py\LoadForecasting\TimeseriesDatasets.py:18: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in th

In [7]:
from WavenetT2V import Wavenet_t2v

wavenet = Wavenet_t2v(6, 31, 3, config = [32, 64, 64, 128, 64], dilatation_rates = [0, 12, 8, 4, 2], outsize = 1)

In [8]:
from tester import ForecastTester

tester = ForecastTester([wavenet], trainds, valds, testds)

In [9]:
tester.train()

c:\Python\lib\site-packages\pytorch_lightning\trainer\connectors\accelerator_connector.py:447: LightningDeprecationWarning:

Setting `Trainer(gpus=1)` is deprecated in v1.7 and will be removed in v2.0. Please use `Trainer(accelerator='gpu', devices=1)` instead.

GPU available: True (cuda), used: True
TPU available: False, using: 0 TPU cores
IPU available: False, using: 0 IPUs
HPU available: False, using: 0 HPUs
LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]

  | Name     | Type       | Params
----------------------------------------
0 | blocks   | ModuleList | 0     
1 | time_emb | t2v        | 217   
2 | wavenet  | WaveNet    | 1.1 M 
----------------------------------------
1.1 M     Trainable params
0         Non-trainable params
1.1 M     Total params
4.474     Total estimated model params size (MB)


Sanity Checking: 0it [00:00, ?it/s]

c:\Python\lib\site-packages\pytorch_lightning\trainer\connectors\data_connector.py:236: PossibleUserWarning:

The dataloader, val_dataloader 0, does not have many workers which may be a bottleneck. Consider increasing the value of the `num_workers` argument` (try 8 which is the number of cpus on this machine) in the `DataLoader` init to improve performance.

c:\Python\lib\site-packages\pytorch_lightning\trainer\connectors\data_connector.py:236: PossibleUserWarning:

The dataloader, train_dataloader, does not have many workers which may be a bottleneck. Consider increasing the value of the `num_workers` argument` (try 8 which is the number of cpus on this machine) in the `DataLoader` init to improve performance.



Training: 0it [00:00, ?it/s]

Validation: 0it [00:00, ?it/s]

...

Validation: 0it [00:00, ?it/s]

Validation: 0it [00:00, ?it/s]

Validation: 0it [00:00, ?it/s]

Validation: 0it [00:00, ?it/s]

`Trainer.fit` stopped: `max_epochs=25` reached.


In [18]:
import pytorch_lightning as pl

model = tester.testers[0].model

test_loader = tester.testers[0].testdl
scaler = tester.testers[0].trainds.scaler

preds = []
ys = []

for x, t, y in test_loader:
    print(x.shape, t.shape, y.shape)
    pred = model(x, t)
    preds.append(pred.detach().numpy())
    ys.append(y.detach().numpy())



torch.Size([32, 336, 1]) torch.Size([32, 336, 6]) torch.Size([32, 336, 1])
torch.Size([32, 336, 1]) torch.Size([32, 336, 6]) torch.Size([32, 336, 1])
torch.Size([13, 336, 1]) torch.Size([13, 336, 6]) torch.Size([13, 336, 1])


In [19]:
preds = np.concatenate(preds)
ys = np.concatenate(ys)

preds.shape, ys.shape

((77, 336, 1), (77, 336, 1))

In [20]:
preds = preds.reshape(-1, 1)
ys = ys.reshape(-1, 1)

preds = scaler.inverse_transform(preds)
ys = scaler.inverse_transform(ys)

preds = preds.reshape(-1)
ys = ys.reshape(-1)

In [21]:
print(test_df['time'].values[:25872].shape, preds.shape, ys.shape)
predsdf = pd.DataFrame({'time':test_df['time'].values[:25872], 'pred': preds, 'y': ys})

(25872,) (25872,) (25872,)


In [22]:
predsdf.head(10)

time         pred            y
0 2018-07-01 00:00:00  2315.698486  2265.495850
1 2018-07-01 00:30:00  2189.997803  2197.644531
2 2018-07-01 01:00:00  2192.511230  2129.812744
3 2018-07-01 01:30:00  2103.707520  2099.013184
4 2018-07-01 02:00:00  2075.809082  2070.062012
5 2018-07-01 02:30:00  2042.635376  2041.572510
6 2018-07-01 03:00:00  2011.277222  2031.584595
7 2018-07-01 03:30:00  1990.840820  2025.410889
8 2018-07-01 04:00:00  1984.256470  1986.520752
9 2018-07-01 04:30:00  1967.882935  1957.303955

In [23]:
px.line(predsdf, x='time', y=['pred', 'y'], title='Load in Cyprus')

In [24]:
# r2 score, mae, mse, rmse

from sklearn.metrics import r2_score, mean_absolute_error, mean_squared_error
print("r2 score: ", r2_score(predsdf['y'], predsdf['pred']))
print("mae: ", mean_absolute_error(predsdf['y'], predsdf['pred']))
print("mse: ", mean_squared_error(predsdf['y'], predsdf['pred']))
print("rmse: ", np.sqrt(mean_squared_error(predsdf['y'], predsdf['pred'])))

r2 score:  0.9386280715581607
mae:  97.60108
mse:  21895.844
rmse:  147.97244


In [ ]:
# save output

predsdf.to_csv('preds.csv', index=False)